### Name :  W16 作業2
### Function : Application of NER and Topic Model 

#### 用蔡適應的資料跑NER

In [33]:
import tensorflow as tf
import keras
import pandas as pd
import numpy as np
import gc
import math
import jieba
from tqdm import tqdm
import matplotlib.pyplot as plt
from collections import Counter

##  function Extract_NER():   Extract NER from receiving text list

In [4]:
def Extract_NER(ls_textRow):
    from ckiptagger import data_utils, construct_dictionary, WS, POS, NER
    
    # 載入 自訂詞典
    User_Dict = {}
    with open("KCC Data/Dict/KccDict2020.txt","r", encoding='utf-8-sig') as UDicts:
        for udic in UDicts:
            udWord = udic.strip().split(" ")
            if len(udWord) > 1:
                User_Dict[udWord[0]] = udWord[1]
            else:
                User_Dict[udWord[0]] = 10    # 未給定權重者一律賦予預設值 10                
    dictionary = construct_dictionary(User_Dict)
 
    ws = WS("./data")
    pos = POS("./data")
    ner = NER("./data")
    
    #  ls_segRow = ws(ls_textRow) ------------   without User Dictionary
    ls_segRow = ws(ls_textRow, 
                   sentence_segmentation=True,
                   segment_delimiter_set = {",", "。", ":", "?", "!", ";", "、"},
                   coerce_dictionary = dictionary)
    #print("ls_segRow = ", ls_segRow)
    #print("-----------------------------")
    
    del ws
    del WS
    gc.collect()
    ls_posRow = pos(ls_segRow)
    del pos
    del POS
    gc.collect()
    ls_nerRow = ner(ls_segRow,ls_posRow)
    del ner
    del NER
    gc.collect()
    #print("ls_nerRow = ", ls_nerRow)
    #print("-----------------------------")
    return ls_nerRow

## 1. Read data from csv or xlsx file

In [5]:
df = pd.read_csv('transcript_0806_1002.csv',encoding='utf-8') #匯資料
df.head(1)

屆期  會期       會議日期   開議時間 會議類型            會次  \
0   8   6  9/12/2014  09:00   院會  第8屆第6會期第1次會議   

                                                  時程 委員姓名     區域      開始時間  \
0  一、12日上午9時至10時為國是論壇時間。二、行政院院長施政報告並備質詢。三、16日下午1時...  柯建銘  全國不分區  16:08:58   

       結束時間  來源1        時長                                        來源2  \
0  16:39:36  NaN  00:30:38  http://ivod.ly.gov.tw/Play/VOD/76016/300K   

                                                 逐字稿  
0  ﻿柯委員建銘：（16 時 8 分）主席、行政院江院長、毛副院長、各部會首長、各位同仁。剛才江...

In [6]:
#讀檔

df_file = pd.read_csv('transcript_0806_1002.csv',encoding='utf-8')
print(df_file.columns)
print("-----------------------------------------------------------")
df_file.head(3)

Index(['屆期', '會期', '會議日期', '開議時間', '會議類型', '會次', '時程', '委員姓名', '區域', '開始時間',
       '結束時間', '來源1', '時長', '來源2', '逐字稿'],
      dtype='object')
-----------------------------------------------------------


屆期  會期       會議日期   開議時間 會議類型            會次  \
0   8   6  9/12/2014  09:00   院會  第8屆第6會期第1次會議   
1   8   6  9/12/2014  09:00   院會  第8屆第6會期第1次會議   
2   8   6  9/12/2014  09:00   院會  第8屆第6會期第1次會議   

                                                  時程 委員姓名        區域      開始時間  \
0  一、12日上午9時至10時為國是論壇時間。二、行政院院長施政報告並備質詢。三、16日下午1時...  柯建銘     全國不分區  16:08:58   
1  一、12日上午9時至10時為國是論壇時間。二、行政院院長施政報告並備質詢。三、16日下午1時...  楊瓊瓔  台中市第3選舉區  15:05:38   
2  一、12日上午9時至10時為國是論壇時間。二、行政院院長施政報告並備質詢。三、16日下午1時...  邱文彥     全國不分區  19:52:28   

       結束時間                                        來源1        時長  \
0  16:39:36                                        NaN  00:30:38   
1  15:36:53                                        NaN  00:31:15   
2  20:23:20  http://ivod.ly.gov.tw/Demand/Speech/76022  00:30:52   

                                         來源2  \
0  http://ivod.ly.gov.tw/Play/VOD/76016/300K   
1  http://ivod.ly.gov.tw/Play/VOD/76015/300K   
2  http://ivod.ly.gov.tw/Play/VOD/76022/300K   

                                                 逐字稿  
0  ﻿柯委員建銘：（16 時 8 分）主席、行政院江院長、毛副院長、各部會首長、各位同仁。剛才江...  
1  ﻿楊委員瓊瓔：（15 時 5 分）主席、行政院江院長、毛副院長、各部會首長、各位同仁。剛剛看...  
2  ﻿邱委員文彥：（19 時52 分）主席、行政院江院長、毛副院長、各部會首長、各位同仁。院長辛...

In [7]:
tsai = df_file[df_file.委員姓名 == "蔡適應"]
tsai

屆期  會期        會議日期   開議時間      會議類型                                 會次  \
9396    9   1    3/4/2016  09:00        院會                       第9屆第1會期第3次會議   
9446    9   1    3/7/2016  09:00  外交及國防委員會        立法院第9屆第1會期外交及國防委員會第2次全體委員會議   
9548    9   1    3/7/2016  14:00  外交及國防委員會  立法院第9屆第1會期外交及國防委員會第2次全體委員會議（增列議程）   
9679    9   1    3/9/2016  09:00  外交及國防委員會        立法院第9屆第1會期外交及國防委員會第3次全體委員會議   
9796    9   1   3/10/2016  09:00  外交及國防委員會        立法院第9屆第1會期外交及國防委員會第4次全體委員會議   
...    ..  ..         ...    ...       ...                                ...   
45515  10   2  12/16/2020  09:00  外交及國防委員會      立法院第10屆第2會期外交及國防委員會第19次全體委員會議   
45621  10   2  12/21/2020  09:00  外交及國防委員會      立法院第10屆第2會期外交及國防委員會第20次全體委員會議   
45888  10   2  12/23/2020  14:30     內政委員會   立法院第10屆第2會期內政、外交及國防、經濟委員會第1次聯席會議   
46023  10   2  12/28/2020  09:00  外交及國防委員會      立法院第10屆第2會期外交及國防委員會第21次全體委員會議   
46165  10   2   1/29/2021  09:00        院會                第10屆第2會期第1次臨時會第2次會議   

                                                      時程 委員姓名      區域  \
9396   一、4日上午9時至10時進行國是論壇。二、對行政院院長提出施政方針及施政報告繼續質詢。三、8...  蔡適應  基隆市選舉區   
9446           邀請外交部部長林永樂報告業務概況暨馬英九總統出訪「久安專案」之籌備概況，並備質詢。  蔡適應  基隆市選舉區   
9548   下午：邀請國防部部長高廣圻率憲兵指揮部指揮官、法務部部長羅瑩雪報告「憲兵非法搜查事件」，並備質詢。  蔡適應  基隆市選舉區   
9679                              邀請國防部部長高廣圻報告業務概況，並備質詢。  蔡適應  基隆市選舉區   
9796                           邀請僑務委員會委員長陳士魁報告業務概況，並備質詢。  蔡適應  基隆市選舉區   
...                                                  ...  ...     ...   
45515  審查110年度中央政府總預算案附屬單位預算關於國防部主管非營業基金： 一、作業基金： （一）...  蔡適應  基隆市選舉區   
45621  一、併案審查：（一）行政院函請審議「護照條例第四條、第十六條及第三十五條之一條文修正草案」案...  蔡適應  基隆市選舉區   
45888  一、審查行政函請審議，及委員管碧玲等19人、委員洪申翰等18人、委員陳亭妃等17人、委員王美...  蔡適應  基隆市選舉區   
46023  邀請外交部部長率領事事務局局長、僑務委員會、交通部、衛生福利部、內政部、勞動部、大陸委員會報...  蔡適應  基隆市選舉區   
46165                                         詳見議事日程（草案）  蔡適應  基隆市選舉區   

           開始時間      結束時間                                         來源1  \
9396   18:12:37  18:42:27   http://ivod.ly.gov.tw/Demand/Speech/85735   
9446   11:23:00  11:35:33   http://ivod.ly.gov.tw/Demand/Speech/85801   
9548   16:01:44  16:16:04   http://ivod.ly.gov.tw/Demand/Speech/85853   
9679   10:58:59  11:14:19   http://ivod.ly.gov.tw/Demand/Speech/86043   
9796   11:03:41  11:16:52   http://ivod.ly.gov.tw/Demand/Speech/86131   
...         ...       ...                                         ...   
45515  11:49:23  11:58:04  http://ivod.ly.gov.tw/Demand/Speech/126749   
45621  11:03:42  11:10:23  http://ivod.ly.gov.tw/Demand/Speech/126938   
45888  15:19:24  15:26:24                                         NaN   
46023  12:09:17  12:18:36  http://ivod.ly.gov.tw/Demand/Speech/127289   
46165  13:36:21  13:39:43                                         NaN   

             時長                                         來源2  \
9396   00:29:50   http://ivod.ly.gov.tw/Play/VOD/85735/300K   
9446   00:12:33   http://ivod.ly.gov.tw/Play/VOD/85801/300K   
9548   00:14:20   http://ivod.ly.gov.tw/Play/VOD/85853/300K   
9679   00:15:20   http://ivod.ly.gov.tw/Play/VOD/86043/300K   
9796   00:13:11   http://ivod.ly.gov.tw/Play/VOD/86131/300K   
...         ...                                         ...   
45515  00:08:41  http://ivod.ly.gov.tw/Play/VOD/126749/300K   
45621  00:06:41  http://ivod.ly.gov.tw/Play/VOD/126938/300K   
45888  00:07:00  http://ivod.ly.gov.tw/Play/VOD/127147/300K   
46023  00:09:19  http://ivod.ly.gov.tw/Play/VOD/127289/300K   
46165  00:03:22  http://ivod.ly.gov.tw/Play/VOD/127470/300K   

                                                     逐字稿  
9396   ﻿蔡委員適應：（18 時 13 分）主席、行政院張院長、杜副院長、各部會首長、各位同仁。延續...  
9446   ﻿蔡委員適應：主席、各位列席官員、各位同仁。部長好！我想今天最「夯」的議題、早上大家在立\n...  
9548   ﻿蔡委員適應：主席、各位列席官員、各位同仁。本席要先請教部長，你今天報告的標題是什麼？\n主...  
9679   ﻿蔡委員適應：主席、各位列席官員、各位同仁。今天主要是就國防部的業務報告來作說明，在作業\n...  
9796   ﻿蔡委員適應：主席、各位列席官員、各位同仁。這次馬英九總統出訪中美洲，請問僑委會有沒有派\n...  
...                                                  ...  
45515  ﻿蔡委員適應：（11 時 49 分）主席、各位列席官員、各位同仁。最近這兩天對軍方來講滿重要...  
45621  ﻿蔡委員適應：（11時3分）主席、各位列席官員、各位同仁。我想請教國防部副部長一個海軍的

In [8]:
tsai_out = tsai[['屆期','會期', '會議日期', '委員姓名', '逐字稿']] #提出會用到的欄位
tsai_out

屆期  會期        會議日期 委員姓名  \
9396    9   1    3/4/2016  蔡適應   
9446    9   1    3/7/2016  蔡適應   
9548    9   1    3/7/2016  蔡適應   
9679    9   1    3/9/2016  蔡適應   
9796    9   1   3/10/2016  蔡適應   
...    ..  ..         ...  ...   
45515  10   2  12/16/2020  蔡適應   
45621  10   2  12/21/2020  蔡適應   
45888  10   2  12/23/2020  蔡適應   
46023  10   2  12/28/2020  蔡適應   
46165  10   2   1/29/2021  蔡適應   

                                                     逐字稿  
9396   ﻿蔡委員適應：（18 時 13 分）主席、行政院張院長、杜副院長、各部會首長、各位同仁。延續...  
9446   ﻿蔡委員適應：主席、各位列席官員、各位同仁。部長好！我想今天最「夯」的議題、早上大家在立\n...  
9548   ﻿蔡委員適應：主席、各位列席官員、各位同仁。本席要先請教部長，你今天報告的標題是什麼？\n主...  
9679   ﻿蔡委員適應：主席、各位列席官員、各位同仁。今天主要是就國防部的業務報告來作說明，在作業\n...  
9796   ﻿蔡委員適應：主席、各位列席官員、各位同仁。這次馬英九總統出訪中美洲，請問僑委會有沒有派\n...  
...                                                  ...  
45515  ﻿蔡委員適應：（11 時 49 分）主席、各位列席官員、各位同仁。最近這兩天對軍方來講滿重要...  
45621  ﻿蔡委員適應：（11時3分）主席、各位列席官員、各位同仁。我想請教國防部副部長一個海軍的問題...  
45888  ﻿蔡委員適應：（15時19分）主席、各位列席官員、各位同仁。請問次長，我們的領海基線是誰管理...  
46023  ﻿蔡委員適應：（12時9分）主席、各位列席官員、各位同仁。我想請教次長一下，上次疫情中心有說...  
46165                                             ﻿無公報記錄  

[263 rows x 5 columns]

In [9]:
tsai_out.reset_index(inplace=True)
tsai_out

index  屆期  會期        會議日期 委員姓名  \
0     9396   9   1    3/4/2016  蔡適應   
1     9446   9   1    3/7/2016  蔡適應   
2     9548   9   1    3/7/2016  蔡適應   
3     9679   9   1    3/9/2016  蔡適應   
4     9796   9   1   3/10/2016  蔡適應   
..     ...  ..  ..         ...  ...   
258  45515  10   2  12/16/2020  蔡適應   
259  45621  10   2  12/21/2020  蔡適應   
260  45888  10   2  12/23/2020  蔡適應   
261  46023  10   2  12/28/2020  蔡適應   
262  46165  10   2   1/29/2021  蔡適應   

                                                   逐字稿  
0    ﻿蔡委員適應：（18 時 13 分）主席、行政院張院長、杜副院長、各部會首長、各位同仁。延續...  
1    ﻿蔡委員適應：主席、各位列席官員、各位同仁。部長好！我想今天最「夯」的議題、早上大家在立\n...  
2    ﻿蔡委員適應：主席、各位列席官員、各位同仁。本席要先請教部長，你今天報告的標題是什麼？\n主...  
3    ﻿蔡委員適應：主席、各位列席官員、各位同仁。今天主要是就國防部的業務報告來作說明，在作業\n...  
4    ﻿蔡委員適應：主席、各位列席官員、各位同仁。這次馬英九總統出訪中美洲，請問僑委會有沒有派\n...  
..                                                 ...  
258  ﻿蔡委員適應：（11 時 49 分）主席、各位列席官員、各位同仁。最近這兩天對軍方來講滿重要...  
259  ﻿蔡委員適應：（11時3分）主席、各位列席官員、各位同仁。我想請教國防部副部長一個海軍的問題...  
260  ﻿蔡委員適應：（15時19分）主席、各位列席官員、各位同仁。請問次長，我們的領海基線是誰管理...  
261  ﻿蔡委員適應：（12時9分）主席、各位列席官員、各位同仁。我想請教次長一下，上次疫情中心有說...  
262                                             ﻿無公報記錄  

[263 rows x 6 columns]

## 2.  Main function:
### 2.1  Pass text data to function "Extract_NER" by row
### 2.2  Integrate every 10 NER return rows into one data frame  
### 2.3  Write frame into small csv after droping duplicate, locating class, filtering short NER, sorting by class.. 

In [10]:
#逐筆傳遞欄位 "text"
tsai_text = tsai_out["逐字稿"]
print("逐字稿 欄位筆數 = ",len(tsai_text))
print("------------------------------------------")
ls_class = list()
ls_ner = list()
fileCunt = 0
rowCunt = 0
for i in range(len(tsai_text)):
    rowCunt += 1
    ls_dfRow = [tsai_text[i]]
    # print("ls_dfRow = ", ls_dfRow)
    print("Row No = ",str(i))
    entity_list = Extract_NER(ls_dfRow)
    for j in range(len(entity_list[0])):
        seg = entity_list[0].pop()
        # print("seg = ",seg)
        ls_class.append(seg[2])
        ls_ner.append(seg[3])
    #print("===========================================")
    #print("ls_class = ",ls_class)
    #print("ls_ner = ",ls_ner)
    # if i == 5 or rowCunt == 2:
    if i == (len(tsai_text)-1) or rowCunt == 10:
        fileCunt += 1
        extract_df = pd.DataFrame({'Class':ls_class, 'NER':ls_ner})
        deDup_df = extract_df.drop_duplicates().copy()
        del extract_df #去除重複
        cate_df = deDup_df.loc[deDup_df['Class'].isin(['LOC','PERSON', 'ORG', 'LAW', 'EVENT','GPE','NORP'])].copy()
        del deDup_df
        filt_df = cate_df[cate_df['NER'].map(len) >= 2].copy()
        del cate_df
        NER_df = filt_df.sort_values(by=['Class']).copy()
        del filt_df
        #print("__________________________________________________________")  
        #print(NER_df)
        print("fileCunt No = ",str(fileCunt))
        NER_df.to_csv(r"News Data\News NER Out\\NewsNER870_" + str(fileCunt)+ ".csv")
        #NER_df.to_csv(r"ner out/NerTest_" + str(fileCunt)+ ".csv")
        rowCunt = 0
print("=====================================================================")
print("Totle NER Files = ",fileCunt)


逐字稿 欄位筆數 =  263
------------------------------------------
Row No =  0


C:\Users\CHING TING\anaconda3\lib\site-packages\tensorflow\python\keras\layers\legacy_rnn\rnn_cell_impl.py:909: UserWarning: `tf.nn.rnn_cell.LSTMCell` is deprecated and will be removed in a future version. This class is equivalent as `tf.keras.layers.LSTMCell`, and will be replaced by that in Tensorflow 2.0.
  warnings.warn("`tf.nn.rnn_cell.LSTMCell` is deprecated and will be "
C:\Users\CHING TING\anaconda3\lib\site-packages\tensorflow\python\keras\engine\base_layer_v1.py:1700: UserWarning: `layer.add_variable` is deprecated and will be removed in a future version. Please use `layer.add_weight` method instead.
  warnings.warn('`layer.add_variable` is deprecated and '


KeyboardInterrupt: 

## 3. Integrate all csv files into single data frame

In [11]:
import glob
# import pandas as pd

path = r'News Data\News NER OUT'
#path = r'ner out'
allFiles = glob.glob("{}/*.csv".format(path))
li = []
for filename in allFiles:
    df = pd.read_csv(filename, index_col=0, header=0)
    li.append(df)

nerFrame = pd.concat(li, axis=0, ignore_index=True)
print(len(nerFrame))
nerFrame.groupby('Class').count()

40750


NER
Class        
EVENT    1321
GPE      6515
LAW       887
LOC      2696
NORP     1829
ORG     15919
PERSON  11583

## 4. Drop duplicates, group by class and write into csv file 

In [12]:
ddFrame = nerFrame.drop_duplicates().copy()
print(len(ddFrame))
ddFrame.groupby('Class').count()

4033


NER
Class       
EVENT    113
GPE      587
LAW       96
LOC      289
NORP     110
ORG     1507
PERSON  1331

In [13]:
ddFrame.sort_values(by=['Class']).to_csv(r"News Data\News NER OUT\\NewsNER.csv")
#ddFrame.sort_values(by=['Class']).to_csv(r"ner out/NerTest.csv")

#### 用蔡適應的資料跑TOPIC MODEL

In [37]:
text_list = list(tsai_out['逐字稿']) # 把所有message轉成一個list 用for iterate

tsai_str = ','.join(text_list)
print(tsai_str) #轉字串斷詞

﻿蔡委員適應：（18 時 13 分）主席、行政院張院長、杜副院長、各部會首長、各位同仁。延續剛才
費委員所提問題，剛才行政院張院長說，您有看到聯合晚報頭版頭的新聞，對不對？本席請陸委
會夏主委上台備詢。
照我們的立院前輩費委員的講法，說這個有問題。院長看到這條新聞之後，你認同它裡面所
講的東西嗎？
張院長善政：（18 時 14 分）主席、各位委員。那個新聞我沒有看完整，您講的是哪個部分？
蔡委員適應：它說監督條例的審查內容會讓我們的公務員不願意上場談判，因為會動輒得咎，光跑
法院法院就夠了，誰還會來幫國家跟人民談判做事。
張院長善政：你講的是，如果談判被認為有問題的話，會被起訴七年以上有期徒刑。
蔡委員適應：對，你同意嗎？我想兩岸談判是陸委會的官員。
夏主任委員立言：以陸委會的官員為主，包括……
蔡委員適應：你同意他們的說法嗎？
夏主任委員立言：因為它裡面用的語氣比較含糊，以現在用的文字來講，譬如，侵犯主權、領土。
以貿易談判為例，什麼叫做侵害到國家主權？這是有定義上問題。
蔡委員適應：好，你擔心這個問題嘛！我想請教院長，我們的談判人員在外面談判，如果真的侵犯
了國家主權，你會同意這樣的談判結果嗎？
張院長善政：這要看您如何定義主權……
蔡委員適應：所以你是移送，還是你自己決定？

張院長善政：我剛才說要看什麼叫主權，譬如稅，叫不叫主權？
蔡委員適應：當然可分為經濟主權及政治主權，我的意思是如果有違反主權，是不是代表你們內部
就會把他移送按相關法律程序辦理？這個反應是沒有錯的嘛！
張院長善政：如果認定在稅方面讓的比較多，就被看成讓利與侵犯主權……
蔡委員適應：你講得很好，因為擔心這個問題，所以需要有兩岸監督條例，對不對？我看到行政院
版本有一個「臺灣地區與大陸地區訂定協議處理及監督條例草案」，其中第十三條也有相關的保
密義務。我覺得民進黨委員提出的這幾個版本，把這個東西再次拿出來，跟我們刑法的相關規定
還是有部分是契合的，這也是提醒未來參與談判的所有人員要恪遵法律規定，我覺得重點精神在
此。我也要拜託夏主委在回到陸委會之後，告訴陸委會的所有官員要有信心，在兩岸監督條例通
過之後，陸委會官員對於未來的兩岸談判只要按照監督條例辦事，我相信是絕對不會有問題的。
我在此首先要請院長及主委在會後回去對相關人員做一說明。
其次，很多人都詢問過院長您是不是「看守內閣」？院長的許多

In [38]:
from ckiptagger import data_utils, construct_dictionary, WS, POS, NER
import gc
import tensorflow as tf
# import keras

# 載入 ckiptagger 自訂詞典
User_Dict = {}
with open("KCC Data/Dict/KccDict2020.txt","r", encoding='utf-8-sig') as UDicts:
    for udic in UDicts:
        udWord = udic.strip().split(" ")
        if len(udWord) > 1:
            User_Dict[udWord[0]] = udWord[1]
        else:
            User_Dict[udWord[0]] = 100    # 未給定權重者一律賦予預設值 100               
dictionary = construct_dictionary(User_Dict)

In [39]:
# 載入模型
ws = WS("./data")
# pos = POS("./data")
# ner = NER("./data")

C:\Users\CHING TING\anaconda3\lib\site-packages\tensorflow\python\keras\layers\legacy_rnn\rnn_cell_impl.py:909: UserWarning: `tf.nn.rnn_cell.LSTMCell` is deprecated and will be removed in a future version. This class is equivalent as `tf.keras.layers.LSTMCell`, and will be replaced by that in Tensorflow 2.0.
  warnings.warn("`tf.nn.rnn_cell.LSTMCell` is deprecated and will be "
C:\Users\CHING TING\anaconda3\lib\site-packages\tensorflow\python\keras\engine\base_layer_v1.py:1700: UserWarning: `layer.add_variable` is deprecated and will be removed in a future version. Please use `layer.add_weight` method instead.
  warnings.warn('`layer.add_variable` is deprecated and '
Exception ignored in: <function POS.__del__ at 0x000001C6225A91F0>
Traceback (most recent call last):
  File "C:\Users\CHING TING\anaconda3\lib\site-packages\ckiptagger\api.py", line 185, in __del__
    self.model.sess.close()
AttributeError: 'POS' object has no attribute 'model'


In [40]:
# 載入 StopWord
stopword_list = []
with open("KCC Data/Dict/KccStopWord2020.txt","r", encoding='utf-8-sig') as stopwords:
    for stopword in stopwords:
        stopword_list.append(stopword.strip())

In [41]:
# 開始斷詞
# sentence_segmentation = True,  => To consider delimiters
# segment_delimiter_set = {",", "。", ":", "?", "!", ";"}), # This is the defualt set of delimiters
# recommend_dictionary = dictionary1, # words in this dictionary are encouraged
# coerce_dictionary = dictionary2, # words in this dictionary are forced
strCut = ws([tsai_str], sentence_segmentation=True,
                 segment_delimiter_set = {'"',"\r\n","，","「","」",",","？",'\n', "。", ":", "?", "!", ";", "、"},
                 coerce_dictionary = dictionary)

print("------------CKIPTagger Word Segment ws(tsai_str,....) + 刪除標點及停用字 ---------------")
stayed_lst= [] #斷好字的
for word in strCut[0]:
     # 刪除停用字
    if word not in stopword_list:
        stayed_lst.append(word)
        
print(" ".join(stayed_lst))

------------CKIPTagger Word Segment ws(tsai_str,....) + 刪除標點及停用字 ---------------
﻿ 蔡 委員 18   時  13   分 行政院 張 院長 杜 副院長 部會 首長 位 同仁 延續 
 費 委員 提 行政院 張 院長 說 聯合晚報 頭版頭 新聞 本席 請 陸委
 夏 主委 上台 備詢 
 立院 前輩費 委員 講法 說 院長 條 新聞 認同 裡面 
 講 東西 
 張 院長 善政 18   時  14   分 委員 新聞 完整 講 
 蔡 委員 說 監督 條例 審查 內容 公務員 上場 談判 動輒得咎 跑 
 法院 法院 夠 幫 國家 談判 做 事 
 張 院長 善政 講 談判 起訴 年 有期徒刑 
 蔡 委員 想 兩岸 談判 陸委會 官員 
 夏 主任委員 立言 陸委會 官員 包括 
 蔡 委員 說法 
 夏 主任委員 立言 裡面 語氣 含糊 文字 講 侵犯 主權 領土 
 貿易 談判 例 侵害到 國家 主權 定義 
 蔡 委員 擔心 想 請教 院長 談判 人員 外面 談判 真的 侵犯 
 國家 主權 談判 
 張 院長 善政 定義 主權 
 蔡 委員 移送 
 
 張 院長 善政 說 主權 稅 主權 
 蔡 委員 分為 經濟 主權 政治 主權 違反 主權 代表 內部 
 移送 相關 法律 程序 辦理 錯 
 張 院長 善政 認定 稅 看成 讓利 侵犯 主權 
 蔡 委員 講 擔心 需要 兩岸監督條例 行政院 
 版本 臺灣 地區 大陸 地區 訂定 協議 監督 條例 草案 第十三 條 相關 保
 密 義務 民進黨 委員 提出 版本 東西 拿出來 刑法 相關 
 契合 提醒 參與 談判 人員 恪遵 法律 重點 精神 
 拜託 夏 主委 回到 陸委會 告訴 陸委會 官員 信心 兩岸監督條例 通
 陸委會 官員 兩岸 談判 監督 條例 辦事 
 請 院長 主委 回去 相關 人員 做 
 詢問 院長 看守 內閣 院長 回答 說 過渡 內閣 
 請問 院長 知不知道 馬英九總統 任命 行政院 長 位 記得 位 
 張 院長 善政 院長 從從 從義 院長   院長 院長 治 院長 
 
 蔡 委員 錯 記得 問 行政院 長 
 過渡 院長 時 任內 政策 有沒有 做下去 有沒有 講 
 講 官腔

In [47]:
fList = []
with open("KCC Data/tsai_Dict.txt","r", encoding='utf-8-sig') as files:
     for file in files:
        #simple_preprocess: tokenize,去除標點 - gensim.utils.simple_preprocess(doc, deacc=False, min_len=2, max_len=15) 
        fList.append(list(utils.simple_preprocess(file, deacc=True, min_len=2,)))
print("fList[:2] = ", fList[:2])
print("------------------------------")

fList[:2] =  [['委員', '行政院', '院長', '副院長', '部會', '首長', '同仁', '延續'], ['委員', '行政院', '院長', '聯合晚報', '頭版頭', '新聞', '本席', '陸委']]
------------------------------


In [48]:
dict = corpora.Dictionary(fList)
print("dict = ", dict)
print("------------------------------")

dict =  Dictionary(14393 unique tokens: ['副院長', '同仁', '委員', '延續', '行政院']...)
------------------------------


In [49]:
# creat mapping matrix of [word_id, word_frequency] for each word segment
corpus = [dict.doc2bow(text) for text in fList]   
print("corpus[:1] = ", corpus[:1])   
print("------------------------------")

print("print lists of [word:frequency]")
[[print((dict[id], freq)) for id,freq in cp] for cp in corpus[:1]]
print("======================================================")

corpus[:1] =  [[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1)]]
------------------------------
print lists of [word:frequency]
('副院長', 1)
('同仁', 1)
('委員', 1)
('延續', 1)
('行政院', 1)
('部會', 1)
('院長', 1)
('首長', 1)


In [51]:
lda_model = models.ldamodel.LdaModel(corpus=corpus, id2word= dict, num_topics=10, passes=20, alpha='auto', chunksize=50, per_word_topics=True)
# print(ldamodel.print_topics())   列出最重要的前若干个主题

output = open("KCC Data/NewsCisTest-KccDict2020-LDA-TopicNum10_tsai.txt", 'w', encoding='utf-8-sig')
lstTM = lda_model.print_topics(num_topics=10, num_words=20)
for tupleTM in lstTM:
        str1 = "".join(str(x) for x in tupleTM)
        #print("type(str1) = ", type(str1))
        str1 += "\n"
        print("strTM = ", str1)
        output.write(str1)
output.close()
 
print("------------------------------")
print("Perplexity = ", lda_model.log_perplexity(corpus))

print("------------------------------")
cm = CoherenceModel(model=lda_model, texts=list(fList), dictionary=dict, coherence= 'c_v' )
coher_lda = cm.get_coherence()
print("\n Coherence Score: ", coher_lda)

strTM =  00.112*"臺灣" + 0.049*"國家" + 0.036*"運輸" + 0.035*"馬紹爾" + 0.035*"醫療" + 0.027*"大眾" + 0.024*"公布" + 0.024*"談判" + 0.023*"軍人" + 0.022*"正式" + 0.020*"振榮" + 0.019*"最近" + 0.019*"好像" + 0.019*"軍事" + 0.015*"能不能" + 0.014*"經濟部" + 0.013*"條例" + 0.013*"會議" + 0.012*"接觸" + 0.012*"超過"

strTM =  10.100*"目前" + 0.055*"請教" + 0.046*"海軍" + 0.033*"立法院" + 0.031*"同仁" + 0.027*"麻煩" + 0.026*"秘書" + 0.026*"規劃" + 0.024*"原因" + 0.020*"資料" + 0.019*"基隆" + 0.017*"海外" + 0.017*"中心" + 0.017*"訓練" + 0.016*"救援" + 0.014*"疫情" + 0.013*"參考" + 0.012*"曉得" + 0.012*"議題" + 0.012*"委員長"

strTM =  20.202*"委員" + 0.040*"部長" + 0.026*"參謀長" + 0.017*"外交部" + 0.017*"相關" + 0.017*"美國" + 0.016*"副部長" + 0.015*"瞭解" + 0.012*"單位" + 0.011*"副主任委員" + 0.010*"第一" + 0.009*"提到" + 0.009*"院長" + 0.009*"執行" + 0.009*"關係" + 0.008*"釗燮" + 0.008*"公報" + 0.008*"請問" + 0.008*"德發" + 0.008*"更新"

strTM =  30.084*"國防部" + 0.074*"報告" + 0.055*"時間" + 0.052*"人員" + 0.051*"局長" + 0.048*"處長" + 0.044*"過程" + 0.033*"發現" + 0.030*"事實" + 0.021*"明年" + 0.016*"交通部" + 0.016*"國正" + 0.016*"紀錄" + 0

In [52]:
import pyLDAvis
import pyLDAvis.gensim #import pyLDAvis.gensim_models
import matplotlib.pyplot as plt
%matplotlib inline

C:\Users\CHING TING\anaconda3\lib\site-packages\sklearn\linear_model\_least_angle.py:34: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  method='lar', copy_X=True, eps=np.finfo(np.float).eps,
C:\Users\CHING TING\anaconda3\lib\site-packages\sklearn\linear_model\_least_angle.py:164: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  method='lar', 

In [53]:
pyLDAvis.enable_notebook
vis = pyLDAvis.gensim.prepare(lda_model, corpus, dict, doc_topic_dist=None)
"""
参数说明：
prepare(topic_model, corpus, dictionary, doc_topic_dist=None)
topic_model：训练得到的 gensim LdaModel 对象，不支持其他 gensim 模型类型
corpus：以词袋形式表示的语料（用于训练主题模型的语料）
dictionary：用于构建词袋模型的字典，即 gensim Dictionary 对象
doc_topic_dist：可选参数，用于传入 LDA 模型的文档主题分布，默认取值为 None，当需要多次调用 prepare 函数时，可以传入该参数
"""
pyLDAvis.display(vis)

C:\Users\CHING TING\anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
